Dies sind ergänzende Plots und Simulationen zu meiner Ausarbeitung zum Thema "Zeitdiskrete Markovketten". Wer nicht nur "meine" Plots anschauen möchte, sondern die Parameter selbst wählt bzw. ergänzende Plots erstellen möchte, findet den Code unter:
https://github.com/mwien/jupyter/blob/master/Seminar.ipynb
Wer sich für die theoretischen Aspekte interessiert, findet meine Ausarbeitung und die Folien des dazugehörigen Vortrags unter den folgenden Links.
- Folien: https://github.com/mwien/jupyter/blob/master/pres.pdf
- Ausarbeitung: https://github.com/mwien/jupyter/blob/master/markov.pdf

In [1]:
using Plots;
Plots.plotly();

In [2]:
function plot_birth_death_process(b, d, N)
    # create the matrix D
    D = zeros(N+1, N+1);
    D[1,1] = 1;
    for i = 2:N
        D[i, i-1] = d[i];
        D[i, i] = - b[i] - d[i];
        D[i, i+1] = b[i];
    end
    D[N+1, N] = d[N+1];
    D[N+1, N+1] = -d[N+1];
    # create the vector c
    c = ones(N+1);
    c *= -1;
    c[1] = 0;
    # calculate the expected extinction time
    τ = D^(-1)*c;
    # plot result
    x = collect(0:N);
    Plots.plot(x,τ, xlab = "Startpopulation", ylab = "Erwartete Aussterbezeit", label = "τ_k", title = "Erwartete Zeit bis zum Aussterben einer Population")
end


plot_birth_death_process (generic function with 1 method)

In [ ]:
Für Geburts- und Todesprozesse hat die Frage nach der Aussterbedauer zentrale Bedeutung.
Wir betrachten diese für mit der Größe der Population linear ansteigende Geburts- bzw. Todeswahrscheinlichkeiten.

In [5]:
br = 0.03;
dr = 0.02;
N = 20;
b = collect(0:N)*br
d = collect(0:N)*dr
Plots.plot(collect(0:20), [b,d, b+d], xlab = "i", ylabel = "p_i", label = ["b" "d" "b+d"], title = "Geburts- und Todeswahrscheinlichkeiten")

In [6]:
plot_birth_death_process(b, d, N)

In [ ]:
Wählt man die Geburts- und Todeswahrscheinlichkeiten nicht beliebig (wie zuvor), sondern dem logistischen Wachstum
nachempfunden, so stabilisiert sich die Population merklich und die Aussterbedauer steigt wesentlich an.

In [7]:
r = 0.015;
K = 10;
N = 20;
b = [r*(i - i^2/(2*K)) for i = 0:N];
d = [r*i^2/(2*K) for i = 0:N];
Plots.plot(collect(1:20), [b,d, b+d],xlab = "i", ylabel = "p_i", label = ["b" "d" "b+d"], title = "Geburts- und Todeswahrscheinlichkeiten")

In [8]:
plot_birth_death_process(b, d, N)

In [9]:
r = 0.015;
K = 10;
N = 20;
b = [r*i for i = 0:N-1];
append!(b, 0)
d = [r*i^2/K for i = 0:N];
Plots.plot(collect(0:20), [b,d, b+d],xlab = "i", ylabel = "p_i", label = ["b" "d" "b+d"], title = "Geburts- und Todeswahrscheinlichkeiten")

In [10]:
plot_birth_death_process(b, d, N)

In [ ]:
Weil es so lange dauert bis die Population ausstirbt, ist es plausibel sich anzuschauen, was bis dahin geschieht.
Dazu simulieren wir die Wahrscheinlichkeitsverteilung für 1000 Schritte.

In [11]:
function plot_dist(b, d, N, rep, X)
    for i = 2:rep
        for j = 0:N
            X[i,j+1] += X[i-1, j+1]*(1-d[j+1]-b[j+1])
            (j > 1) && (X[i,j+1] += X[i-1,j]*b[j])
            (j < N) && (X[i,j+1] += X[i-1,j+2]*d[j+2])
        end
    end
    Plots.surface(collect(0:N), collect(1:rep), X, color = :pu_or, xlab = "Populationsgröße", ylab = "Zeit", zlab = "Wahrscheinlichkeit", title = "Verteilung eines logistischen Wachstumsprozesses")
end

plot_dist (generic function with 1 method)

In [12]:
r = 0.015;
K = 10;
N = 20;
rep = 1000;
X = zeros(rep, N+1);
X[1,2] = 1; 
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_dist(b,d,N,rep, X)

In [13]:
r = 0.015;
K = 10;
N = 20;
rep = 1000;
X = zeros(rep, N+1);
X[1,2] = 1; 
b = [r*i for i = 0:N-1];
append!(b, 0)
d = [r*i^2/K for i = 0:N];
plot_dist(b,d,N, rep, X)

In [14]:
r = 0.004;
K = 50;
N = 100;
rep = 2000;
X = zeros(rep, N+1);
X[1,6] = 1;
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_dist(b,d,N,rep, X)

In [ ]:
Es fällt auf, dass sich die Populationsgröße um den Wert $K = 50$ einpendelt, mal abgesehen von den Fällen bei denen die Population ausstirbt.
Wir vergleichen daher den Mittelwert des stochastischen Prozesses mit dem deterministischen logistischen Wachstum.

In [15]:
function plot_comp(b, d, N, rep, X, K, r, x0)
    for i = 2:rep
        for j = 0:N
            X[i,j+1] += X[i-1, j+1]*(1-d[j+1]-b[j+1])
            (j > 1) && (X[i,j+1] += X[i-1,j]*b[j])
            (j < N) && (X[i,j+1] += X[i-1,j+2]*d[j+2])
        end
    end
    f(x) = 5*K*exp(r*x) / (5*exp(r*x) + K - 5);
    y = [f(x) for x = 1:rep];
    Plots.plot(collect(1:rep), [X*collect(0:N), y], xlab = "Zeit", ylab = "Populationsgröße", label = ["Erwartungswert des stoch. Prozesses" "Deterministisches Modell"], title = "Vergleich der Modelle");
end

plot_comp (generic function with 1 method)

In [16]:
r = 0.004;
K = 50;
N = 100;
rep = 2000;
X = zeros(rep, N+1);
X[1,6] = 1;
x0 = 5;
b = [r*(i - i^2/(2*K)) for i = 0:2*K];
d = [r*i^2/(2*K) for i = 0:2*K];
plot_comp(b, d, N, rep, X, K, r, x0)

In [ ]:
Es zeigt sich das beide Modelle durchaus Ähnlichkeiten besitzen, vorausgesetzt die Population stirbt nicht aus.
Dies ist unsere Motivation für die quasistationäre Verteilung bei der genau dieser Fall ausgeschlossen wird.
Hier kann nun eine (quasi)stationäre Verteilung berechnet werden.

In [17]:
function get_quasistationary(b,d,N)
    # create the matrix D
    D = zeros(N, N);
    for i = 1:N
        (i > 1) && (D[i, i-1] = b[i-1]);
        D[i, i] = 1 - b[i] - d[i];
        (i < N) && (D[i, i+1] = d[i+1]);
    end
    # calculate the eigenvectors
    (W, V) = eig(D);
    ind = [abs(W[i] - 1) < 1e-9 for i = 1:N];
    y = V[:, ind];
    y /= sum(y);
    return(y);
end

get_quasistationary (generic function with 1 method)

In [18]:
r = 0.004;
K = 50;
N = 100;
b = [r*(i - i^2/(2*K)) for i = 1:2*K];
d = [r*i^2/(2*K) for i = 1:2*K];
print("value of d[1]: ", d[1], "\n")
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", real(sum(collect(1:N).*q)))

value of d[1]: 4.0e-5
Mean: 49.489573970775574

In [19]:
Plots.plot(collect(1:N), real(q), xlab = "Populationsgröße", ylab = "Wahrscheinlichkeit", label = "q", title = "Quasistationäre Verteilung")

In [20]:
r = 0.015;
K = 10;
N = 20;
b = [r*(i - i^2/(2*K)) for i = 1:2*K];
d = [r*i^2/(2*K) for i = 1:2*K];
print("value of d[1]: ", d[1], "\n")
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", sum(collect(1:20).*q))

value of d[1]: 0.00075
Mean: 9.434825819217039

In [21]:
Plots.plot(collect(1:N), q, xlab = "Populationsgröße", ylab = "Wahrscheinlichkeit", label = "q", title = "Quasistationäre Verteilung")

In [22]:
r = 0.015;
K = 10;
N = 20;
b = [r*i for i = 1:N-1];
append!(b, 0)
d = [r*i^2/K for i = 1:N];
print("value of d[1]: ", d[1], "\n")
d[1] = 0;
q = get_quasistationary(b,d,N)
print("Mean: ", sum(collect(1:N).*q))

value of d[1]: 0.0015
Mean: 8.839552850381859

In [23]:
Plots.plot(collect(1:N), q, xlab = "Populationsgröße", ylab = "Wahrscheinlichkeit", label = "q", title = "Quasistationäre Verteilung")